# Prepare session

In [1]:
import boto3
import sagemaker
from sagemaker import get_execution_role
from sagemaker.local import LocalSession
import s3fs
import subprocess
from sagemaker.s3 import S3Downloader, S3Uploader
from pathlib import Path
import json

image_name = "sagemaker-aishield"
ecr_namespace = image_name + "/"
default_bucket = "prod-aicovidvn"
default_uri = "s3://" + default_bucket
atf_s3_uri = default_uri + "/sagemaker-aishield"

role = get_execution_role()
account_id = role.split(":")[4]
boto_session = boto3.Session()
region = boto_session.region_name
bucket = default_bucket

sagemaker_session = LocalSession(boto_session=boto_session)
sagemaker_session._default_bucket = default_bucket
    
s3_helper = s3fs.S3FileSystem()
data_location_uri = default_uri + "/training_data/full"

print(account_id)
print(region)
print(role)
print(sagemaker_session)
print(default_uri)
print(atf_s3_uri)
print(data_location_uri)

852039983533
ap-southeast-1
arn:aws:iam::852039983533:role/service-role/AmazonSageMaker-ExecutionRole-20211022T094935
s3://prod-aicovidvn
s3://prod-aicovidvn/sagemaker
s3://prod-aicovidvn/training_data/full


# Dev in script mode
(Still run locally but using SageMaker API)

## Build image

In [2]:
! cd container && bash build_image.sh $image_name Dockerfile

Sending build context to Docker daemon  19.26MB
Step 1/20 : ARG DEBIAN_FRONTEND=noninteractive
Step 2/20 : FROM ubuntu:18.04
18.04: Pulling from library/ubuntu

Digest: sha256:0fedbd5bd9fb72089c7bbca476949e10593cebed9b1fb9edf5b79dbbacddd7d6[1A
Status: Downloaded newer image for ubuntu:18.04
 ---> 5a214d77f5d7
Step 3/20 : MAINTAINER Amazon AI <sage-learner@amazon.com>
 ---> Running in 68d417ae487c
Removing intermediate container 68d417ae487c
 ---> 7e70898a68b3
Step 4/20 : RUN apt-get update
 ---> Running in 4a6abdc03fde
Get:1 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic InRelease [242 kB]
Get:3 http://security.ubuntu.com/ubuntu bionic-security/restricted amd64 Packages [666 kB]
Get:4 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Get:5 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [74.6 kB]
Get:6 http://security.ubuntu.com/ubuntu bionic-security/universe amd64 Packages [1442 kB]
Get

## Prepare data

In [3]:
opt_ml_dir = "/opt/ml/processing"
execution_id = "exp-local-sm"
image_uri = f"{image_name}:latest"
print(image_uri)

sagemaker-top3:latest


In [4]:
from sagemaker.processing import ScriptProcessor, ProcessingInput, ProcessingOutput

processor = ScriptProcessor(
    base_job_name="prepare-data-processor",
    image_uri=image_uri,
    command=['python'], # IMPORTANT, DEPENDS ON DOCKERFILE, DON'T USE python3
    role=role,
    instance_count=1,
    instance_type="local",
    max_runtime_in_seconds=1200,
)

# IMPORTANT: ProcessingOutput MUST BE A FOLDER WITHOUT ANY NESTED FOLDER INSIDE
# Otherwise it will raise Permission Denied when it performs post processes
# Example: source CANNOT BE "/opt/ml/processing/output/prepared_data" because there're 2 nested folders inside

processor.run(
    code="container/code/prepare_data.py",
    inputs=[
        ProcessingInput(
            source=data_location_uri,
            destination=opt_ml_dir + "/input",
        ),
    ],
    outputs=[
        ProcessingOutput(
            output_name="train",
            source=opt_ml_dir + "/train",
            destination=atf_s3_uri + f"/prepared_data/{execution_id}/train",
        ),
        ProcessingOutput(
            output_name="test",
            source=opt_ml_dir + "/test",
            destination=atf_s3_uri + f"/prepared_data/{execution_id}/test",
        )
    ],
    arguments=[""],
    wait=True,
    logs=True,
)

Stopping condition is not supported in local mode.



Job Name:  prepare-data-processor-2021-11-24-02-53-57-098
Inputs:  [{'InputName': 'input-1', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://prod-aicovidvn/training_data/full', 'LocalPath': '/opt/ml/processing/input', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'code', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-ap-southeast-1-852039983533/prepare-data-processor-2021-11-24-02-53-57-098/input/code/prepare_data.py', 'LocalPath': '/opt/ml/processing/input/code', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}]
Outputs:  [{'OutputName': 'train', 'AppManaged': False, 'S3Output': {'S3Uri': 's3://prod-aicovidvn/sagemaker/prepared_data/exp-local-sm/train', 'LocalPath': '/opt/ml/processing/train', 'S3UploadMode': 'EndOfJob'}}, {'OutputName': 'test', 'AppManaged': False, 'S3Output': {'S3Uri': 's3://prod-aicovidvn

In [5]:
# Inspect uploaded data
preprocessing_job_description = processor.jobs[-1].describe()
output_config = preprocessing_job_description["ProcessingOutputConfig"]
for output in output_config["Outputs"]:
    if output["OutputName"] == "train":
        train_data_uri = output["S3Output"]["S3Uri"]
    if output["OutputName"] == "test":
        test_data_uri = output["S3Output"]["S3Uri"]

! aws s3 ls $train_data_uri/
! aws s3 ls $test_data_uri/

                           PRE scalers/
2021-11-24 02:56:10    1456102 train.csv
2021-11-24 02:56:10     413680 test.csv
2021-11-24 02:56:10       1053 scaler_chroma.save
2021-11-24 02:56:10       5693 scaler_mel.save
2021-11-24 02:56:10       1093 scaler_mfcc.save
2021-11-24 02:56:10        613 scaler_zcr.save


In [6]:
import pandas as pd
s3 = boto3.client('s3')
obj = s3.get_object(Bucket=default_bucket, Key=f'sagemaker/prepared_data/{execution_id}/train/train.csv')
train_df = pd.read_csv(obj['Body']) # 'Body' is a key word
train_df.head()

label     zcr_0    mfcc_0    mfcc_1    mfcc_2    mfcc_3    mfcc_4  \
0      1  0.406804  0.705249  0.192932  0.308788  0.362266  0.601216   
1      1  0.452427  0.335556  0.561600  0.514944  0.558073  0.468664   
2      1  0.481952  0.505047  0.172644  0.575324  0.412500  0.328545   
3      1  0.718777  0.902690  0.156923  0.673243  0.261746  0.551814   
4      1  0.627859  0.317835  0.220190  0.618888  0.535140  0.399838   

     mfcc_5    mfcc_6    mfcc_7  ...       mel_118       mel_119  \
0  0.884194  0.693697  0.555827  ...  1.739178e-01  2.454223e-01   
1  0.353174  0.770820  0.521627  ...  3.352944e-08  2.561214e-08   
2  0.728827  0.200066  0.532453  ...  9.538092e-08  8.009980e-08   
3  0.522708  0.521770  0.392145  ...  7.147761e-01  9.366683e-01   
4  0.812745  0.550459  0.863862  ...  4.105715e-07  4.412555e-08   

        mel_120       mel_121       mel_122       mel_123       mel_124  \
0  4.793423e-01  8.156974e-01  7.228810e-01  8.717778e-02  1.736281e-02   
1  1.129508e-08  6.303398e-09  4.152624e-09  8.598178e-10  4.405661e-10   
2  6.436375e-08  6.289963e-08  8.049304e-08  2.631158e-08  3.583820e-08   
3  6.891887e-01  7.633957e-01  6.234479e-01  1.822659e-01  2.106632e-01   
4  2.122575e-08  1.381480e-08  1.079715e-08  6.123927e-09  6.729353e-09   

        mel_125       mel_126       mel_127  
0  5.678505e-04  3.503496e-07  5.835581e-07  
1  6.049370e-10  1.175339e-09  8.730436e-09  
2  9.286300e-08  1.299997e-07  6.767989e-07  
3  2.987725e-01  2.762438e-01  3.735656e-01  
4  2.029002e-08  3.072942e-08  1.496800e-07  

[5 rows x 155 columns]

In [7]:
train_df.columns

Index(['label', 'zcr_0', 'mfcc_0', 'mfcc_1', 'mfcc_2', 'mfcc_3', 'mfcc_4',
       'mfcc_5', 'mfcc_6', 'mfcc_7',
       ...
       'mel_118', 'mel_119', 'mel_120', 'mel_121', 'mel_122', 'mel_123',
       'mel_124', 'mel_125', 'mel_126', 'mel_127'],
      dtype='object', length=155)

## Train

In [8]:
import sagemaker
import json

# JSON encode hyperparameters
def json_encode_hyperparameters(hyperparameters):
    return {str(k): json.dumps(v) for (k, v) in hyperparameters.items()}

hyperparameters = json_encode_hyperparameters({
    "learning_rate": 0.0001,
    "batch_size": 50,
    "epochs": 10
})

est = sagemaker.estimator.Estimator(
    image_uri,
    role,
    instance_count=1,
    instance_type="local",
    hyperparameters=hyperparameters,
    output_path=atf_s3_uri + f"/model",
    sagemaker_session=sagemaker_session,
)

est.fit({"train": train_data_uri})

Creating j20mmymttg-algo-1-u51rn ... 
Creating j20mmymttg-algo-1-u51rn ... done
Attaching to j20mmymttg-algo-1-u51rn
j20mmymttg-algo-1-u51rn | params: {'learning_rate': '0.05'}
j20mmymttg-algo-1-u51rn | Start inspect_input
j20mmymttg-algo-1-u51rn | /opt/ml/input/data: ['train']
j20mmymttg-algo-1-u51rn | /opt/ml/input/data/train: ['train.csv', 'scalers']
j20mmymttg-algo-1-u51rn | /opt/ml/input/data/train/scalers: ['scaler_mel.save', 'scaler_mfcc.save', 'scaler_chroma.save', 'scaler_zcr.save']
j20mmymttg-algo-1-u51rn | Start train
j20mmymttg-algo-1-u51rn | Training with params={'objective': 'binary', 'boosting_type': 'gbdt', 'metric': 'auc', 'learning_rate': 0.05, 'subsample': 0.68, 'tree_learner': 'serial', 'colsample_bytree': 0.28, 'early_stopping_rounds': 100, 'subsample_freq': 1, 'reg_lambda': 2, 'reg_alpha': 1, 'num_leaves': 500, 'random_state': 42}
j20mmymttg-algo-1-u51rn | Seed: 0
j20mmymttg-algo-1-u51rn | (444, 154) (444,)
j20mmymttg-algo-1-u51rn | /usr/local/lib/python3.8/dist-p

In [9]:
job_name = est.latest_training_job.name
print(job_name)

sagemaker-top3-2021-11-24-02-56-27-529


In [10]:
training_job_description = est.jobs[-1].describe()
model_data_s3_uri = f"{training_job_description['ModelArtifacts']['S3ModelArtifacts']}"
model_data_s3_uri

's3://prod-aicovidvn/sagemaker/model/sagemaker-top3-2021-11-24-02-56-27-529/model.tar.gz'

## Evaluate

In [11]:
print(test_data_uri)

s3://prod-aicovidvn/sagemaker/prepared_data/exp-local-sm/test


In [12]:
from sagemaker.processing import ScriptProcessor, ProcessingInput, ProcessingOutput

eval_processor = ScriptProcessor(
    base_job_name="evaluate-processor",
    image_uri=image_uri,
    command=['python'],
    role=role,
    instance_count=1,
    instance_type="local",
    max_runtime_in_seconds=1200,
)

eval_processor.run(
    code="container/code/evaluate.py",
    inputs=[
        ProcessingInput(
            source=model_data_s3_uri,
            destination=opt_ml_dir + "/model",
        ),
        ProcessingInput(
            source=test_data_uri,
            destination=opt_ml_dir + "/test",
        ),
    ],
    outputs=[
        ProcessingOutput(
            output_name="evaluation",
            source=opt_ml_dir + "/evaluation",
            destination=atf_s3_uri + f"/evaluation/{execution_id}",
        ),
    ],
    arguments=[""],
    wait=True,
    logs=True,
)

Stopping condition is not supported in local mode.



Job Name:  evaluate-processor-2021-11-24-03-00-03-146
Inputs:  [{'InputName': 'input-1', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://prod-aicovidvn/sagemaker/model/sagemaker-top3-2021-11-24-02-56-27-529/model.tar.gz', 'LocalPath': '/opt/ml/processing/model', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'input-2', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://prod-aicovidvn/sagemaker/prepared_data/exp-local-sm/test', 'LocalPath': '/opt/ml/processing/test', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'code', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-ap-southeast-1-852039983533/evaluate-processor-2021-11-24-03-00-03-146/input/code/evaluate.py', 'LocalPath': '/opt/ml/processing/input/code', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated'

In [13]:
eval_job_description = eval_processor.jobs[-1].describe()
eval_output_config = eval_job_description["ProcessingOutputConfig"]
for output in eval_output_config["Outputs"]:
    if output["OutputName"] == "evaluation":
        eval_uri = output["S3Output"]["S3Uri"]
        
! aws s3 ls $eval_uri/

2021-11-24 03:00:09        152 eval.json


## Deploy

In [14]:
from sagemaker.predictor import CSVSerializer
predictor = est.deploy(
    initial_instance_count=1,
    instance_type="local",
    serializer=CSVSerializer(),
)

Attaching to tjoddy5576-algo-1-vvqpo
tjoddy5576-algo-1-vvqpo | Starting the inference server with 4 workers.
tjoddy5576-algo-1-vvqpo | [2021-11-24 03:01:27 +0000] [11] [INFO] Starting gunicorn 20.1.0
tjoddy5576-algo-1-vvqpo | [2021-11-24 03:01:27 +0000] [11] [INFO] Listening at: unix:/tmp/gunicorn.sock (11)
tjoddy5576-algo-1-vvqpo | [2021-11-24 03:01:27 +0000] [11] [INFO] Using worker: sync
tjoddy5576-algo-1-vvqpo | [2021-11-24 03:01:27 +0000] [14] [INFO] Booting worker with pid: 14
tjoddy5576-algo-1-vvqpo | [2021-11-24 03:01:27 +0000] [15] [INFO] Booting worker with pid: 15
tjoddy5576-algo-1-vvqpo | [2021-11-24 03:01:27 +0000] [19] [INFO] Booting worker with pid: 19
tjoddy5576-algo-1-vvqpo | [2021-11-24 03:01:27 +0000] [20] [INFO] Booting worker with pid: 20
!tjoddy5576-algo-1-vvqpo | 172.18.0.1 - - [24/Nov/2021:03:01:29 +0000] "GET /ping HTTP/1.1" 200 1 "-" "python-urllib3/1.26.7"


In [15]:
endpoint_name = predictor.endpoint_name
print(endpoint_name)

sagemaker-top3-2021-11-24-03-01-24-145


## Test endpoint

In [16]:
test_data = train_df.drop(train_df.columns[[0]], axis=1)
test_data.head()

zcr_0    mfcc_0    mfcc_1    mfcc_2    mfcc_3    mfcc_4    mfcc_5  \
0  0.406804  0.705249  0.192932  0.308788  0.362266  0.601216  0.884194   
1  0.452427  0.335556  0.561600  0.514944  0.558073  0.468664  0.353174   
2  0.481952  0.505047  0.172644  0.575324  0.412500  0.328545  0.728827   
3  0.718777  0.902690  0.156923  0.673243  0.261746  0.551814  0.522708   
4  0.627859  0.317835  0.220190  0.618888  0.535140  0.399838  0.812745   

     mfcc_6    mfcc_7    mfcc_8  ...       mel_118       mel_119  \
0  0.693697  0.555827  0.227635  ...  1.739178e-01  2.454223e-01   
1  0.770820  0.521627  0.592784  ...  3.352944e-08  2.561214e-08   
2  0.200066  0.532453  0.358474  ...  9.538092e-08  8.009980e-08   
3  0.521770  0.392145  0.553889  ...  7.147761e-01  9.366683e-01   
4  0.550459  0.863862  0.584510  ...  4.105715e-07  4.412555e-08   

        mel_120       mel_121       mel_122       mel_123       mel_124  \
0  4.793423e-01  8.156974e-01  7.228810e-01  8.717778e-02  1.736281e-02   
1  1.129508e-08  6.303398e-09  4.152624e-09  8.598178e-10  4.405661e-10   
2  6.436375e-08  6.289963e-08  8.049304e-08  2.631158e-08  3.583820e-08   
3  6.891887e-01  7.633957e-01  6.234479e-01  1.822659e-01  2.106632e-01   
4  2.122575e-08  1.381480e-08  1.079715e-08  6.123927e-09  6.729353e-09   

        mel_125       mel_126       mel_127  
0  5.678505e-04  3.503496e-07  5.835581e-07  
1  6.049370e-10  1.175339e-09  8.730436e-09  
2  9.286300e-08  1.299997e-07  6.767989e-07  
3  2.987725e-01  2.762438e-01  3.735656e-01  
4  2.029002e-08  3.072942e-08  1.496800e-07  

[5 rows x 154 columns]

### Test endpoint using predict function

In [17]:
results = predictor.predict(test_data.values).decode('utf-8')
list(map(float, results.split('\n')[:-1]))

tjoddy5576-algo-1-vvqpo | Invoked with 460 records
tjoddy5576-algo-1-vvqpo | 172.18.0.1 - - [24/Nov/2021:03:01:38 +0000] "POST /invocations HTTP/1.1" 200 8842 "-" "python-urllib3/1.26.7"


[0.5255793577357346,
 0.49460133334307627,
 0.8432777986352242,
 0.8439706243746231,
 0.6901743243070613,
 0.8863093539803873,
 0.846367402306896,
 0.8182954652528269,
 0.8233453262914553,
 0.9060134756684242,
 0.5998151807600993,
 0.9071585851683072,
 0.7839652358526843,
 0.7109876129028551,
 0.77811852472689,
 0.826506610360956,
 0.8780013183323091,
 0.7893861301241946,
 0.9070461487917931,
 0.8222024108490277,
 0.8040008689022065,
 0.7857836046841316,
 0.4341007772060095,
 0.6453497501624443,
 0.8026213566918606,
 0.6171794701083433,
 0.8059604163663532,
 0.8713190970210847,
 0.7698274983247007,
 0.879772423760417,
 0.8819344265897223,
 0.8077860790562137,
 0.8329409300545616,
 0.8671033109903397,
 0.7901879567569244,
 0.875117983864148,
 0.6644790015179599,
 0.7280487132508184,
 0.5243794458946252,
 0.7114181541426242,
 0.5659939950074923,
 0.7985720840213419,
 0.8993327179986338,
 0.849068385559527,
 0.8867240255803259,
 0.8173055684905972,
 0.7683145132734325,
 0.6995425304563756

### Test endpoint using Curl

In [18]:
test_data_str = CSVSerializer().serialize(test_data.values)
payload_file = "./payload"
with open(payload_file, "w") as f:
    f.write(test_data_str)
    
curl_str = f"""\
curl -X POST \
http://localhost:8080/invocations \
--data-binary @{payload_file} \
-H 'Content-Type: text/csv'\
"""
curl_str

"curl -X POST http://localhost:8080/invocations --data-binary @./payload -H 'Content-Type: text/csv'"

In [19]:
subprocess.run(curl_str, shell=True).stderr

tjoddy5576-algo-1-vvqpo | Invoked with 460 records
tjoddy5576-algo-1-vvqpo | 172.18.0.1 - - [24/Nov/2021:03:01:57 +0000] "POST /invocations HTTP/1.1" 200 8867 "-" "curl/7.71.1"


In [20]:
predictor.delete_endpoint()

Gracefully stopping... (press Ctrl+C again to force)


In [21]:
! rm payload